In [1]:
import os #print(os.getcwd())
import random
import mplcursors
%matplotlib inline
import numpy as np
import pandas as pd
import plotly.io as pio
import plotly.express as px
import plotly.offline as pyo
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from scipy.spatial import cKDTree
import plotly.graph_objects as go
from prophet.plot import plot, plot_components

pio.renderers.default='notebook' #svg

In [2]:
def get_random_ren_additions(years: int, mean: int, std_dev=20000, min_value=0, max_value=70000):
    additions = np.random.normal(loc=mean, scale=std_dev, size=years)
    if max_value is not None:
        while np.any(additions > max_value) or np.any(additions < min_value):
            additions = np.where((additions > max_value) | (additions < min_value), 
                                 np.random.normal(loc=mean, scale=std_dev, size=years), 
                                 additions)
    return additions

ren_additions = get_random_ren_additions(years=13, mean=65000)
print(ren_additions)

[36920.81672116 69761.54032639 69572.20935886 57685.56533176
 48156.47408484 34942.0984633  65189.17274226 65457.7686559
 65059.40340675 47188.98459078 68352.20042904 37664.41311027
 62004.80480473]


In [6]:
def get_random_non_ren_additions(years: int, start=2000, end=10000):    
    return np.random.randint(start, end+1, years).tolist()
non_ren_additions = get_random_non_ren_additions(years=6)
print(non_ren_additions)

[8601, 2208, 4725, 5955, 9850, 3993]


In [7]:
def get_random_ren_retirements(years: int, start=0, end=1000):
    return np.random.randint(start, end+1, years).tolist()
ren_retirements = get_random_ren_retirements(years=6)
print(ren_retirements)

[553, 694, 238, 420, 250, 332]


# 1. Ideal Solution

In [7]:
def get_random_ren_additions(years: int, mean: int, std_dev=20000, max_value=70000):
    additions = np.random.normal(loc=mean, scale=std_dev, size=years)
    while np.any(additions > max_value):
        additions[additions > max_value] = np.random.normal(loc=mean, scale=std_dev, size=np.sum(additions > max_value))
    return additions
    
def get_random_non_ren_additions(years: int, start=2000, end=10000):    
    return np.random.randint(start, end+1, years).tolist()
    
def get_random_ren_retirements(years: int, start=0, end=100):
    return np.random.randint(start, end+1, years).tolist()

def get_random_non_ren_retirements(years: int, start=10000, end=20000):    
    return np.random.randint(start, end+1, years).tolist()

def get_confidence_levels(final_capacities):    
    upper_confidence = round(np.quantile(final_capacities, 0.975), 2)
    lower_confidence = round(np.quantile(final_capacities, 0.025), 2)
    
    return lower_confidence, upper_confidence

def get_yearly_percentiles(cumulatives, inputs, percentiles=[5, 50, 95]):
    """
    Calculate yearly percentiles for a list of cumulative capacity simulations.
    
    Parameters:
    - cumulatives: List of lists containing cumulative capacity values for each simulation.
    - inputs: Dictionary containing the input parameters, including start_age and end_age.
    - percentiles: List of percentiles to calculate. Default is [5, 50, 95].
    
    Returns:
    - Dictionary where keys are years and values are dictionaries of the calculated percentiles.
    """
    start_age = inputs['start_age']
    end_age = inputs['end_age']
    years = end_age - start_age
    
    # Initialize a dictionary to hold the percentiles for each year
    yearly_percentiles = {year: {} for year in range(start_age, end_age)}
    
    # Convert the list of lists into a numpy array for easier percentile calculation
    cumulatives_array = np.array(cumulatives)
    
    for i in range(years):
        yearly_values = cumulatives_array[:, i]
        for p in percentiles:
            yearly_percentiles[start_age + i][p] = np.percentile(yearly_values, p)
    
    return yearly_percentiles

In [24]:
def plot_simulations(cumulatives, title, xaxis_title, yaxis_title, inputs):
    years = list(range(inputs['start_age'], inputs['end_age']))

    # Plot the simulations
    fig = go.Figure()

    for simulation in cumulatives:
        fig.add_trace(go.Scatter(x=years, y=simulation, mode='lines', line=dict(width=0.5), opacity=0.3, name='Capacity'))

    fig.update_layout(
        title=title,
        xaxis_title=xaxis_title,
        yaxis_title=yaxis_title,
        showlegend=False
    )

    fig.show()

In [21]:
def plot_histogram(final_capacities: list, 
                   upper_confidence:float, 
                   lower_confidence: float):
    """
    Plots the frequencies of the final capacities.
    """
    fig = px.histogram(final_capacities, 
                       title=f"The final capacity after {len(final_capacities)} simulations.")
    
    fig.add_vline(x=lower_confidence, 
                  line_width=3, 
                  line_dash="dash", 
                  line_color="green")
    
    fig.add_vline(x=upper_confidence, 
                  line_width=3, 
                  line_dash="dash", 
                  line_color="green")
    
    fig.add_vline(x=np.median(final_capacities), 
                  line_width=3, 
                  line_dash="dash", 
                  line_color="black",
                  annotation_text="median",
                  annotation_font_size=15)
    
    fig.add_vrect(x0=lower_confidence, 
                  x1=upper_confidence, 
                  line_width=0, 
                  fillcolor="green",
                  opacity=0.2,
                  annotation_text="95% confidence interval",
                  annotation_font_size=15)
    
    fig.update_layout(
        xaxis_title="Capacity (MW)",
        yaxis_title="Count",
        showlegend=False,
        font=dict(
            family="Arial",
            size=14
        ),
        paper_bgcolor='rgba(0,0,0,0)',
        plot_bgcolor='rgba(0,0,0,0)',
    )
    
    fig.show()

In [87]:
def plot_yearly_percentiles(yearly_percentiles, title='Yearly Percentiles', ylabel='Capacity (MW)', 
                                   target=None, target_label=None):

    years = list(yearly_percentiles.keys())
    if not years:
        print("No data available to plot.")
        return
    
    # Determine which percentiles are available
    example_year = years[0]
    available_percentiles = yearly_percentiles[example_year].keys()
    
    traces = []
    
    # Plot available percentiles
    for p in available_percentiles:
        traces.append(go.Scatter(
            x=years,
            y=[yearly_percentiles[year][p] for year in years],
            mode='lines',
            name=f'{p}th Percentile'
        ))
    
    # Shaded areas for specific ranges, if they exist
    if 5 in available_percentiles and 95 in available_percentiles:
        traces.append(go.Scatter(
            x=years,
            y=[yearly_percentiles[year][5] for year in years],
            fill=None,
            mode='lines',
            line=dict(color='gray', width=0.5),
            showlegend=False
        ))
        traces.append(go.Scatter(
            x=years,
            y=[yearly_percentiles[year][95] for year in years],
            fill='tonexty',
            mode='lines',
            line=dict(color='gray', width=0.5),
            fillcolor='rgba(128, 128, 128, 0.2)',
            name='5th-95th Percentile Range'
        ))

    if 25 in available_percentiles and 75 in available_percentiles:
        traces.append(go.Scatter(
            x=years,
            y=[yearly_percentiles[year][25] for year in years],
            fill=None,
            mode='lines',
            line=dict(color='blue', width=0.5),
            showlegend=False
        ))
        traces.append(go.Scatter(
            x=years,
            y=[yearly_percentiles[year][75] for year in years],
            fill='tonexty',
            mode='lines',
            line=dict(color='blue', width=0.5),
            fillcolor='rgba(0, 0, 255, 0.2)',
            name='25th-75th Percentile Range'
        ))

    # Plot target line
    if target is not None:
        traces.append(go.Scatter(
            x=[years[0], years[-1]],
            y=[target, target],
            mode='lines',
            line=dict(color='red', dash='dash'),
            name=target_label
        ))
        
        # Annotate the year when target is reached
        offset = 0
        for p in available_percentiles:
            target_year = next((year for year in years if yearly_percentiles[year][p] >= target), None)
            if target_year:
                traces.append(go.Scatter(
                    x=[target_year],
                    y=[target],
                    mode='markers+text',
                    text=[f'{p}th Percentile reaches target'],
                    textposition='top right',
                    marker=dict(color='red'),
                    showlegend=False
                ))
                offset += target * 0.05  # Increase offset for the next annotation

    layout = go.Layout(
        title=title,
        xaxis=dict(title='Year'),
        yaxis=dict(title=ylabel),
        legend=dict(x=0.01, y=0.99)
    )
    
    fig = go.Figure(data=traces, layout=layout)
    
    return fig

In [98]:
def plot_combined_yearly_percentiles_plotly(ren_yearly_percentiles, non_ren_yearly_percentiles, 
                                            title='Yearly Percentiles', ylabel='Capacity (MW)', 
                                            ren_target=None, ren_target_label=None,
                                            non_ren_target=None, non_ren_target_label=None):
    """
    Plot the combined yearly percentiles for both renewable and non-renewable using Plotly.

    Parameters:
    - ren_yearly_percentiles: Dictionary containing yearly percentiles for renewables.
    - non_ren_yearly_percentiles: Dictionary containing yearly percentiles for non-renewables.
    - title: Title of the plot.
    - ylabel: Label for the y-axis.
    - ren_target: The renewable target value to be highlighted in the plot.
    - ren_target_label: Label for the renewable target line.
    - non_ren_target: The non-renewable target value to be highlighted in the plot.
    - non_ren_target_label: Label for the non-renewable target line.
    """
    years = list(ren_yearly_percentiles.keys())
    if not years:
        print("No data available to plot.")
        return
    
    # Determine which percentiles are available
    example_year = years[0]
    available_percentiles = ren_yearly_percentiles[example_year].keys()
    
    traces = []
    
    # Plot renewable percentiles
    for p in available_percentiles:
        traces.append(go.Scatter(
            x=years,
            y=[ren_yearly_percentiles[year][p] for year in years],
            mode='lines',
            name=f'Renewable {p}th Percentile'
        ))
    
    # Shaded areas for renewable specific ranges, if they exist
    if 5 in available_percentiles and 95 in available_percentiles:
        traces.append(go.Scatter(
            x=years,
            y=[ren_yearly_percentiles[year][5] for year in years],
            fill=None,
            mode='lines',
            line=dict(color='gray', width=0.5),
            showlegend=False
        ))
        traces.append(go.Scatter(
            x=years,
            y=[ren_yearly_percentiles[year][95] for year in years],
            fill='tonexty',
            mode='lines',
            line=dict(color='gray', width=0.5),
            fillcolor='rgba(128, 128, 128, 0.2)',
            name='Renewable 5th-95th Percentile Range'
        ))

    if 25 in available_percentiles and 75 in available_percentiles:
        traces.append(go.Scatter(
            x=years,
            y=[ren_yearly_percentiles[year][25] for year in years],
            fill=None,
            mode='lines',
            line=dict(color='blue', width=0.5),
            showlegend=False
        ))
        traces.append(go.Scatter(
            x=years,
            y=[ren_yearly_percentiles[year][75] for year in years],
            fill='tonexty',
            mode='lines',
            line=dict(color='blue', width=0.5),
            fillcolor='rgba(0, 0, 255, 0.2)',
            name='Renewable 25th-75th Percentile Range'
        ))

    # Plot non-renewable percentiles
    for p in available_percentiles:
        traces.append(go.Scatter(
            x=years,
            y=[non_ren_yearly_percentiles[year][p] for year in years],
            mode='lines',
            name=f'Non-Renewable {p}th Percentile',
            line=dict(dash='dash')
        ))
    
    # Shaded areas for non-renewable specific ranges, if they exist
    if 5 in available_percentiles and 95 in available_percentiles:
        traces.append(go.Scatter(
            x=years,
            y=[non_ren_yearly_percentiles[year][5] for year in years],
            fill=None,
            mode='lines',
            line=dict(color='orange', width=0.5, dash='dash'),
            showlegend=False
        ))
        traces.append(go.Scatter(
            x=years,
            y=[non_ren_yearly_percentiles[year][95] for year in years],
            fill='tonexty',
            mode='lines',
            line=dict(color='orange', width=0.5, dash='dash'),
            fillcolor='rgba(255, 165, 0, 0.2)',
            name='Non-Renewable 5th-95th Percentile Range'
        ))

    if 25 in available_percentiles and 75 in available_percentiles:
        traces.append(go.Scatter(
            x=years,
            y=[non_ren_yearly_percentiles[year][25] for year in years],
            fill=None,
            mode='lines',
            line=dict(color='red', width=0.5, dash='dash'),
            showlegend=False
        ))
        traces.append(go.Scatter(
            x=years,
            y=[non_ren_yearly_percentiles[year][75] for year in years],
            fill='tonexty',
            mode='lines',
            line=dict(color='red', width=0.5, dash='dash'),
            fillcolor='rgba(255, 0, 0, 0.2)',
            name='Non-Renewable 25th-75th Percentile Range'
        ))

    # Plot target lines
    if ren_target is not None:
        traces.append(go.Scatter(
            x=[years[0], years[-1]],
            y=[ren_target, ren_target],
            mode='lines',
            line=dict(color='green', dash='dash'),
            name=ren_target_label
        ))
        
        # Annotate the year when target is reached for renewables
        for p in available_percentiles:
            target_year = next((year for year in years if ren_yearly_percentiles[year][p] >= ren_target), None)
            if target_year:
                traces.append(go.Scatter(
                    x=[target_year],
                    y=[ren_target],
                    mode='markers+text',
                    text=[f'{p}th Percentile reaches renewable target'],
                    textposition='top right',
                    marker=dict(color='green'),
                    showlegend=False
                ))

    if non_ren_target is not None:
        traces.append(go.Scatter(
            x=[years[0], years[-1]],
            y=[non_ren_target, non_ren_target],
            mode='lines',
            line=dict(color='purple', dash='dash'),
            name=non_ren_target_label
        ))
        
        # Annotate the year when target is reached for non-renewables
        for p in available_percentiles:
            target_year = next((year for year in years if non_ren_yearly_percentiles[year][p] <= non_ren_target), None)
            if target_year:
                traces.append(go.Scatter(
                    x=[target_year],
                    y=[non_ren_target],
                    mode='markers+text',
                    text=[f'{p}th Percentile reaches non-renewable target'],
                    textposition='bottom right',
                    marker=dict(color='purple'),
                    showlegend=False
                ))

    layout = go.Layout(
        title=title,
        xaxis=dict(title='Year'),
        yaxis=dict(title=ylabel),
        legend=dict(x=1.05, y=1, orientation='v')  # Adjust the legend position
    )
    
    fig = go.Figure(data=traces, layout=layout)
    return fig

In [99]:
# Capacity additions & retirements
capacity = 65789

In [100]:
def perform_simulation(inputs: dict):
    capacity = inputs['capacity']
    renewable = inputs['renewable']
    non_renewable = inputs['non_renewable']
    
    years = inputs['end_age'] - inputs['start_age']
        
    ren_additions = get_random_ren_additions(years=years, mean=capacity)
    non_ren_additions = get_random_non_ren_additions(years=years)
    
    ren_retirements = get_random_ren_retirements(years=years)
    non_ren_retirements = get_random_non_ren_retirements(years=years, start=10000, end=capacity)
    
    ren_cumulative = []
    non_ren_cumulative = []
    
    for i in range(years):        
        # Apply capacity additions
        renewable += ren_additions[i]
        non_renewable += non_ren_additions[i]
        
        # Apply capacity retirements        
        renewable -= ren_retirements[i]
        non_renewable -= non_ren_retirements[i]
        
        ren_cumulative.append(int(renewable))
        non_ren_cumulative.append(int(non_renewable))
        
    return renewable, non_renewable, ren_cumulative, non_ren_cumulative

def perform_monte_carlo(inputs: dict, n: int = 1000):
    renewable = []
    non_renewable = []
    ren_cumulatives = []
    non_ren_cumulatives = []
    
    for i in range(n):
        final_ren, final_non_ren, ren_cumulative, non_ren_cumulative = perform_simulation(inputs)
        renewable.append(final_ren)
        non_renewable.append(final_non_ren)
        ren_cumulatives.append(ren_cumulative)
        non_ren_cumulatives.append(non_ren_cumulative)
        
    renewable_lower_confidence, renewable_upper_confidence = get_confidence_levels(renewable)
    non_renewable_lower_confidence, non_renewable_upper_confidence = get_confidence_levels(non_renewable)
    
    ren_percentiles = get_yearly_percentiles(ren_cumulatives, inputs)
    non_ren_percentiles = get_yearly_percentiles(non_ren_cumulatives, inputs)
            
    return {
        'renewable': renewable,
        'non_renewable': non_renewable,
        'ren_cumulatives': ren_cumulatives,
        'non_ren_cumulatives': non_ren_cumulatives,
        'renewable_lower_confidence': renewable_lower_confidence,
        'renewable_upper_confidence': renewable_upper_confidence, 
        'non_renewable_lower_confidence': non_renewable_lower_confidence,
        'non_renewable_upper_confidence': non_renewable_upper_confidence, 
        'ren_yearly_percentiles': get_yearly_percentiles(ren_cumulatives, inputs),
        'non_ren_yearly_percentiles': get_yearly_percentiles(non_ren_cumulatives, inputs),
        
        'ren_percentiles': ren_percentiles,
        'non_ren_percentiles': non_ren_percentiles
    }
    
inputs = {
    'capacity': capacity,
    'start_age': 2022,
    'end_age': 2035,
    'renewable': 332150.6,
    'non_renewable': 724216.7,
    'target_ren_capacity': 980000,
    'target_non_ren_capacity': 0,
    'n_simulations': 10000,
}
mc = perform_monte_carlo(inputs, 
                         n=inputs['n_simulations'])

In [101]:
plot_combined_yearly_percentiles_plotly(mc['ren_yearly_percentiles'], mc['non_ren_yearly_percentiles'], 
                                                                   title='Yearly Percentiles for Renewable and Non-Renewable Capacity', 
                                                                   ylabel='Capacity (MW)', 
                                                                   ren_target=inputs['target_ren_capacity'], 
                                                                   ren_target_label='Renewable Target',
                                                                   non_ren_target=inputs['target_non_ren_capacity'], 
                                                                   non_ren_target_label='Non-Renewable Target')

In [90]:
plot_yearly_percentiles(mc['ren_percentiles'], title='Yearly Percentiles for Renewable Capacity', 
                        ylabel='Renewable Capacity (MW)', target=inputs['target_ren_capacity'], 
                        target_label='Renewable Target')

In [91]:
plot_yearly_percentiles(mc['non_ren_percentiles'], title='Yearly Percentiles for Non-Renewable Capacity', 
                        ylabel='Non-Renewable Capacity (MW)', target=inputs['target_non_ren_capacity'], 
                        target_label='Non-Renewable Target')

In [38]:
plot_simulations(
        mc['ren_cumulatives'], 
        'Monte Carlo Simulations of Renewable Capacity', 
        'Year', 
        'Renewable Capacity', 
        inputs
    )

In [23]:
plot_simulations(
        mc['non_ren_cumulatives'], 
        'Monte Carlo Simulations of Non-Renewable Capacity', 
        'Year', 
        'Non-Renewable Capacity', 
        inputs
    )

# 2. Reality

In [145]:
# Capacity additions
renewable_additions = 44661.3
non_renewable_additions = 2624

#Capacity retirements
renewable_retirements = 12.8
non_renewable_retirements = 4450.7

In [93]:
def get_random_ren_additions(years: int, mean: int, std_dev=5000):
    random_additions = np.random.normal(loc=mean, scale=std_dev, size=years)
    random_additions[0] = 50000
    return random_additions

ren_additions = get_random_ren_additions(years=13, mean=65789)
print(ren_additions)

[50000.         72421.75536929 58439.22263996 58970.85346692
 77402.89268757 61717.34710072 62106.46715859 67658.9657307
 71620.83565976 65103.23499926 68365.16435174 64585.18018487
 68980.40415923]


In [146]:
def get_random_ren_additions(years: int, mean: int, std_dev=5000):
    
    return np.random.normal(loc=mean, scale=std_dev, size=years)
    
def get_random_non_ren_additions(years: int, start=2000, end=10000):    
    return np.random.randint(start, end+1, years).tolist()
    
def get_random_ren_retirements(years: int, start=0, end=100):
    return np.random.randint(start, end+1, years).tolist()

def get_random_non_ren_retirements(years: int, start=10000, end=20000):    
    return np.random.randint(start, end+1, years).tolist()

####################################################

def get_random_ren_additions(mean: int, std_dev: int, years: int, min_value: int, max_value: int):
    return np.random.normal(loc=mean, scale=std_dev, size=years)

def get_random_non_ren_additions(years: int, start=2000, end=10000):    
    return np.random.randint(start, end+1, years).tolist()
    
def get_random_ren_retirements(years: int):
    random_retirements = []
    
    for year in range(years):
        retirement = random.choices(
            population = ['high', 'medium', 'low'],
            weights = [5, 20, 70],
            k = 1
        )[0]

        if retirement == 'high':
            retirement_value = random.randint(200, 300) 
        elif retirement == 'medium':
            retirement_value = random.randint(100, 199)
        else:
            retirement_value = random.randint(0, 99)  

        random_retirements.append(retirement_value)
        
        random_retirements[0] = renewable_retirements
   
    return random_retirements
    
def get_random_non_ren_retirements(years: int):
    random_retirements = []
    
    for year in range(years):
        retirement = random.choices(
            population = ['high', 'medium', 'low'],
            weights = [5, 25, 70],
            k = 1
        )[0]

        if retirement == 'high':
            retirement_value = random.randint(11000, 15000) 
        elif retirement == 'medium':
            retirement_value = random.randint(6000, 10000)
        else:
            retirement_value = random.randint(0, 5000)  

        random_retirements.append(retirement_value)
        
        random_retirements[0] = renewable_retirements
   
    return random_retirements

def get_confidence_levels(pot_sizes):    
    upper_confidence = round(np.quantile(pot_sizes, 0.975), 2)
    lower_confidence = round(np.quantile(pot_sizes, 0.025), 2)
    
    return lower_confidence, upper_confidence

In [126]:
capacity = 65000

In [127]:
def perform_simulation(inputs: dict):
    capacity = inputs['capacity']
    renewable = inputs['renewable']
    non_renewable = inputs['non_renewable']
    
    years = inputs['end_age'] - inputs['start_age']
        
    ren_additions = get_random_ren_additions(mean=capacity, std_dev=5000, years=years, min_value=0, max_value=100000)
    non_ren_additions = get_random_non_ren_additions(years=years, start=2000, end=10000)
    
    ren_retirements = get_random_ren_retirements(years=years)
    non_ren_retirements = get_random_non_ren_retirements(years=years)
    
    ren_cumulative = []
    non_ren_cumulative = []
    
    for i in range(years):        
        # Apply capacity additions
        renewable += ren_additions[i]
        non_renewable += non_ren_additions[i]
        
        # Apply capacity retirements        
        renewable -= ren_retirements[i]
        non_renewable -= non_ren_retirements[i]
        
        ren_cumulative.append(int(renewable))
        non_ren_cumulative.append(int(non_renewable))
        
    return renewable, non_renewable, ren_cumulative, non_ren_cumulative

def perform_monte_carlo(inputs: dict, n: int = 1000):
    renewable = []
    non_renewable = []
    ren_cumulatives = []
    non_ren_cumulatives = []
    
    for i in range(n):
        final_ren, final_non_ren, ren_cumulative, non_ren_cumulative = perform_simulation(inputs)
        renewable.append(final_ren)
        non_renewable.append(final_non_ren)
        ren_cumulatives.append(ren_cumulative)
        non_ren_cumulatives.append(non_ren_cumulative)
        
    renewable_lower_confidence, renewable_upper_confidence = get_confidence_levels(renewable)
    non_renewable_lower_confidence, non_renewable_upper_confidence = get_confidence_levels(non_renewable)
            
    return {
        'renewable': renewable,
        'non_renewable': non_renewable,
        'ren_cumulatives': ren_cumulatives,
        'non_ren_cumulatives': non_ren_cumulatives,
        'renewable_lower_confidence': renewable_lower_confidence,
        'renewable_upper_confidence': renewable_upper_confidence, 
        'non_renewable_lower_confidence': non_renewable_lower_confidence,
        'non_renewable_upper_confidence': non_renewable_upper_confidence, 
        'ren_yearly_percentiles': get_yearly_percentiles(ren_cumulatives, inputs),
        'non_ren_yearly_percentiles': get_yearly_percentiles(non_ren_cumulatives, inputs)
    }
    
inputs = {
    'capacity': capacity,
    'start_age': 2023,
    'end_age': 2035,
    'renewable': 378126.3, #2022 => 'renewable': 332150.6, => + 45975.7
    'non_renewable': 717434.9, #2022 => 'non_renewable': 724216.7, => + 7753.9 - 14535.7
    'target_ren_capacity': 980000,
    'target_non_ren_capacity': 0,
    'n_simulations': 10000,
}
mc = perform_monte_carlo(inputs, 
                         n=inputs['n_simulations'])

In [124]:
plot_yearly_percentiles(inputs=inputs,
                        df=mc['ren_yearly_percentiles'])

In [149]:
plot_yearly_percentiles(inputs=inputs,
                        df=mc['non_ren_yearly_percentiles'])